In [1]:
import os
import sys
sys.path.append('/media/senilab/DATA/Master/I3D-Tensorflow/')
import time
import numpy
from six.moves import xrange  # pylint: disable=redefined-builtin
import tensorflow as tf
import input_test
import math
import numpy as np
from i3d import InceptionI3d
from utils import *

/usr/local/lib/python3.5/dist-packages/tensorflow/python/framework/dtypes.py:526: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/usr/local/lib/python3.5/dist-packages/tensorflow/python/framework/dtypes.py:527: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/usr/local/lib/python3.5/dist-packages/tensorflow/python/framework/dtypes.py:528: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/usr/local/lib/python3.5/dist-packages/tensorflow/python/framework/dtypes.py:529: FutureWarning: Passing (type, 1) or 


For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
If you depend on functionality not listed there, please file an issue.



In [2]:
batch_size = 1
gpu_num = 1
num_frame_per_clib = 16
crop_size = 224
rgb_channels = 3
classics = 101
os.environ["CUDA_VISIBLE_DEVICES"] = "0"

In [3]:
# Get the sets of images and labels for training, validation, and
# Tell TensorFlow that the model will be built into the default Graph.
rgb_pre_model_save_dir = "/media/senilab/DATA/Master/I3D-Tensorflow/experiments/ucf-101/models/rgb_imagenet_10000_101_4_64_0.0001_decay"
flow_pre_model_save_dir = "/media/senilab/DATA/Master/I3D-Tensorflow/experiments/ucf-101/models/flow_imagenet_101_20000_3_64_0.0001_decay"
test_list_file = '/media/senilab/DATA/Master/I3D-Tensorflow/list/ucf_list/test.list'
file = list(open(test_list_file, 'r'))
num_test_videos = len(file)
print("Number of test videos={}".format(num_test_videos))


Number of test videos=3417


In [4]:
with tf.Graph().as_default():
    rgb_images_placeholder, flow_images_placeholder, labels_placeholder, is_training = placeholder_inputs(
                    batch_size * gpu_num,
                    num_frame_per_clib,
                    crop_size,
                    rgb_channels
                    )

    with tf.variable_scope('RGB'):
        rgb_logit, _ = InceptionI3d(
                            num_classes=classics,
                            spatial_squeeze=True,
                            final_endpoint='Logits',
                            name='inception_i3d'
                            )(rgb_images_placeholder, is_training)
    with tf.variable_scope('Flow'):
        flow_logit, _ = InceptionI3d(
                            num_classes=classics,
                            spatial_squeeze=True,
                            final_endpoint='Logits',
                            name='inception_i3d'
                            )(flow_images_placeholder, is_training)
    norm_score = tf.nn.softmax(tf.add(rgb_logit, flow_logit))

    # Create a saver for writing training checkpoints.
    rgb_variable_map = {}
    flow_variable_map = {}
    for variable in tf.global_variables():
        if variable.name.split('/')[0] == 'RGB' and 'Adam' not in variable.name.split('/')[-1] :
            rgb_variable_map[variable.name.replace(':0', '')] = variable
    rgb_saver = tf.train.Saver(var_list=rgb_variable_map, reshape=True)

    for variable in tf.global_variables():
        if variable.name.split('/')[0] == 'Flow'and 'Adam' not in variable.name.split('/')[-1] :
            flow_variable_map[variable.name.replace(':0', '')] = variable
    flow_saver = tf.train.Saver(var_list=flow_variable_map, reshape=True)
    saver = tf.train.Saver()
    init = tf.global_variables_initializer()

    # Create a session for running Ops on the Graph
    config = tf.ConfigProto()
    config.gpu_options.allow_growth = True
    sess = tf.Session(
                    config=config
                    )
    sess.run(init)



Instructions for updating:
Colocations handled automatically by placer.
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.
(1, 1, 1, 1, 1024)
(1, 1, 1, 1, 1024)


In [5]:
# load pre_train models
ckpt = tf.train.get_checkpoint_state(rgb_pre_model_save_dir)
if ckpt and ckpt.model_checkpoint_path:
    print("loading checkpoint %s,waiting......" % ckpt.model_checkpoint_path)
    rgb_saver.restore(sess, ckpt.model_checkpoint_path)
    print("load complete!")
ckpt = tf.train.get_checkpoint_state(flow_pre_model_save_dir)
if ckpt and ckpt.model_checkpoint_path:
    print("loading checkpoint %s,waiting......" % ckpt.model_checkpoint_path)
    flow_saver.restore(sess, ckpt.model_checkpoint_path)
    print("load complete!")

all_steps = num_test_videos
top1_list = []
start_time_all = time.time()


loading checkpoint /media/senilab/DATA/Master/I3D-Tensorflow/experiments/ucf-101/models/rgb_imagenet_10000_101_4_64_0.0001_decay/i3d_ucf_model_scratch-9999,waiting......
Instructions for updating:
Use standard file APIs to check for files with this prefix.
INFO:tensorflow:Restoring parameters from /media/senilab/DATA/Master/I3D-Tensorflow/experiments/ucf-101/models/rgb_imagenet_10000_101_4_64_0.0001_decay/i3d_ucf_model_scratch-9999
load complete!
loading checkpoint /media/senilab/DATA/Master/I3D-Tensorflow/experiments/ucf-101/models/flow_imagenet_101_20000_3_64_0.0001_decay/i3d_ucf_model_scratch-19999,waiting......
INFO:tensorflow:Restoring parameters from /media/senilab/DATA/Master/I3D-Tensorflow/experiments/ucf-101/models/flow_imagenet_101_20000_3_64_0.0001_decay/i3d_ucf_model_scratch-19999
load complete!


In [7]:
for step in xrange(all_steps):
    start_time = time.time()
    s_index = 0
    predicts = []
    top1 = False
    while True:
        rgb_images, flow_images, val_labels, s_index, is_end = input_test.read_clip_and_label(
                        filename=file[step],
                        batch_size=batch_size * gpu_num,
                        s_index=s_index,
                        num_frames_per_clip=num_frame_per_clib,
                        crop_size=crop_size,
                        )
        predict = sess.run(norm_score,
                           feed_dict={
                                        rgb_images_placeholder: rgb_images,
                                        flow_images_placeholder: flow_images,
                                        labels_placeholder: val_labels,
                                        is_training: False
                                        })
        predicts.append(np.array(predict).astype(np.float32).reshape(classics))
        # print ('predict', predict)
        if is_end:
            avg_pre = np.mean(predicts, axis=0).tolist()
            # print ('avg_pred',avg_pre)
            print (avg_pre.index(max(avg_pre)))
            print ('val_label',val_labels)
            top1 = (avg_pre.index(max(avg_pre))==val_labels)
            top1_list.append(top1)
            break
    duration = time.time() - start_time
    print('TOP_1_ACC in test: %f , time use: %.3f' % (top1, duration))
print(len(top1_list))
dur_time_all = time.time() - start_time_all
print('TOP_1_ACC in test_all: %f, time use: %.3f' % (np.mean(top1_list),dur_time_all))
print("done")

Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g01_c03...strat_frame = 0
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g01_c03...strat_frame = 16
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g01_c03...strat_frame = 32
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g01_c03...strat_frame = 48
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g01_c03...strat_frame = 64
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g01_c03...strat_frame = 80
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g01_c03...strat_frame = 96
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g01_c03...strat_frame = 112
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g

Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g04_c02...strat_frame = 16
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g04_c02...strat_frame = 32
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g04_c02...strat_frame = 48
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g04_c02...strat_frame = 64
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g04_c02...strat_frame = 80
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g04_c02...strat_frame = 96
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g04_c02...strat_frame = 112
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g04_c02...strat_frame = 128
0
val_label [0]
TOP_1_ACC in test: 1.000000 , time use: 0.764
Loading a video clip fro

Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g08_c05...strat_frame = 160
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g08_c05...strat_frame = 176
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g08_c05...strat_frame = 192
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g08_c05...strat_frame = 208
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g08_c05...strat_frame = 224
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g08_c05...strat_frame = 240
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g08_c05...strat_frame = 256
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g08_c05...strat_frame = 272
0
val_label [0]
TOP_1_ACC in test: 1.000000 , time use: 1.313
Loading a video cl

Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g15_c01...strat_frame = 160
0
val_label [0]
TOP_1_ACC in test: 1.000000 , time use: 0.798
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g15_c02...strat_frame = 0
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g15_c02...strat_frame = 16
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g15_c02...strat_frame = 32
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g15_c02...strat_frame = 48
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g15_c02...strat_frame = 64
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g15_c02...strat_frame = 80
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g15_c02...strat_frame = 96
Loading a video clip from 

Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g21_c01...strat_frame = 32
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g21_c01...strat_frame = 48
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g21_c01...strat_frame = 64
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g21_c01...strat_frame = 80
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g21_c01...strat_frame = 96
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g21_c01...strat_frame = 112
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g21_c01...strat_frame = 128
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeup_g21_c01...strat_frame = 144
Loading a video clip from /media/senilab/DATA2/UCF-101/ApplyEyeMakeup/v_ApplyEyeMakeu

...

Loading a video clip from /media/senilab/DATA2/UCF-101/WritingOnBoard/v_WritingOnBoard_g21_c07...strat_frame = 256
Loading a video clip from /media/senilab/DATA2/UCF-101/WritingOnBoard/v_WritingOnBoard_g21_c07...strat_frame = 272
Loading a video clip from /media/senilab/DATA2/UCF-101/WritingOnBoard/v_WritingOnBoard_g21_c07...strat_frame = 288
Loading a video clip from /media/senilab/DATA2/UCF-101/WritingOnBoard/v_WritingOnBoard_g21_c07...strat_frame = 304
99
val_label [99]
TOP_1_ACC in test: 1.000000 , time use: 1.959
Loading a video clip from /media/senilab/DATA2/UCF-101/WritingOnBoard/v_WritingOnBoard_g22_c02...strat_frame = 0
Loading a video clip from /media/senilab/DATA2/UCF-101/WritingOnBoard/v_WritingOnBoard_g22_c02...strat_frame = 16
Loading a video clip from /media/senilab/DATA2/UCF-101/WritingOnBoard/v_WritingOnBoard_g22_c02...strat_frame = 32
Loading a video clip from /media/senilab/DATA2/UCF-101/WritingOnBoard/v_WritingOnBoard_g22_c02...strat_frame = 48
Loading a video clip 

Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g01_c02...strat_frame = 160
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g01_c02...strat_frame = 176
100
val_label [100]
TOP_1_ACC in test: 1.000000 , time use: 1.100
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g01_c03...strat_frame = 0
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g01_c03...strat_frame = 16
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g01_c03...strat_frame = 32
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g01_c03...strat_frame = 48
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g01_c03...strat_frame = 64
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g01_c03...strat_frame = 80
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g01_c03...strat_frame = 96
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g01_c03...strat_fram

Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g05_c03...strat_frame = 48
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g05_c03...strat_frame = 64
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g05_c03...strat_frame = 80
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g05_c03...strat_frame = 96
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g05_c03...strat_frame = 112
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g05_c03...strat_frame = 128
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g05_c03...strat_frame = 144
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g05_c03...strat_frame = 160
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g05_c03...strat_frame = 176
100
val_label [100]
TOP_1_ACC in test: 1.000000 , time use: 0.887
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g06_c04...strat_

Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g13_c05...strat_frame = 96
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g13_c05...strat_frame = 112
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g13_c05...strat_frame = 128
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g13_c05...strat_frame = 144
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g13_c05...strat_frame = 160
100
val_label [100]
TOP_1_ACC in test: 1.000000 , time use: 0.848
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g14_c02...strat_frame = 0
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g14_c02...strat_frame = 16
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g14_c02...strat_frame = 32
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g14_c02...strat_frame = 48
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g14_c02...strat_fr

Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g19_c02...strat_frame = 112
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g19_c02...strat_frame = 128
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g19_c02...strat_frame = 144
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g19_c02...strat_frame = 160
55
val_label [100]
TOP_1_ACC in test: 0.000000 , time use: 0.771
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g19_c04...strat_frame = 0
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g19_c04...strat_frame = 16
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g19_c04...strat_frame = 32
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g19_c04...strat_frame = 48
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g19_c04...strat_frame = 64
Loading a video clip from /media/senilab/DATA2/UCF-101/YoYo/v_YoYo_g19_c04...strat_fra